# Name: Mohammad Javad Noroozi
# Student Number: 99102434
# HW3

### import the necessary library

In [1]:
import json
import datetime
from collections import Counter


In [2]:
# For measuring the total running time of this notebook
start_notebook_t = datetime.datetime.now()
print(start_notebook_t)

2024-02-04 13:54:06.711848


In [3]:
import findspark
findspark.find()
findspark.init()

import pyspark
from pyspark.sql import SparkSession
spark = SparkSession \
    .builder \
    .appName("HW1") \
    .master("local[*]") \
    .getOrCreate()

sc=spark.sparkContext


24/02/04 13:54:08 WARN Utils: Your hostname, javad-IdeaPad-Gaming-3-15IAH7 resolves to a loopback address: 127.0.1.1; using 192.168.137.8 instead (on interface enp48s0)
24/02/04 13:54:08 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
24/02/04 13:54:08 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


### Read data

In [4]:
tweets_rdd = sc.textFile("twitter_data_v2.jsonl")


### Downsampling (If your RAM memory is low)

In [5]:
# tweets_rdd = tweets_rdd.sample(False, 0.1, seed=42)


### Show a sample of tweets

In [6]:
tweets_rdd.takeSample(False, 1, 19)

['{"in_reply_to_status_id_str": null, "in_reply_to_user_id_str": null, "in_reply_to_status_id": null, "in_reply_to_user_id": null, "in_reply_to_screen_name": null, "truncated": false, "is_quote_status": false, "retweet_count": 3, "reply_count": 0, "quote_count": 0, "favorite_count": 0, "favorited": false, "retweeted": true, "possibly_sensitive": null, "lang": "fa", "geo": null, "view_count": 0, "tweet_type": "retweeted", "emojis": null, "text": "مردک وطن\u200cفروش بدبخت، ترانه آفتابکاران جنگل مال چی بوده که خوندن؟! موسیقی اصیل ایرانی بوده؟! یا سرود تروریست\u200cهای چریک کمونیست بوده؟!\\nاشکال نداره، شما به خزعبل گویی ادامه بدید. خوبیش اینه که مردم دارن کم کم متوجه میشن که شنا دگوری\u200cهای خائن وطن\u200cفروش چه جماعتی هستید.\\n\\n#ننگ_بر_سه_فاسد_ملا_چپی_مجاهد", "user": {"id": "315689091", "id_str": "315689091", "created_at": 1307868062, "name": "The Nerd", "screen_name": "NewbieBadASS", "location": "خیابون هفده شهریور ", "url": "https://t.co/ajpmxoYoTe", "description": "A supporter of

### Show size of data (No. tweets)

In [7]:
tweets_rdd.count()

4175860

### Extract all user IDs

In [8]:
users = tweets_rdd.map(lambda x: json.loads(x)["user"].get('id')).collect()

### Select a User

In [9]:
'''
you must choose user id in this section.
you can change # in `counts.most_common()[#][0]` for this purpose.
'''
counts = Counter(users)
q_uid = counts.most_common()[50][0]
q_uid = '1365385186364567553'
print('query user id:', q_uid)

query user id: 1365385186364567553


## Extracting the selected user's favorite tweet ids

### Define Parameters for the Primary Rating.

In [10]:
# Define Parameters
owner_s = 1

# following parameters should not be equal to owner_s
rep_to_s = 0.2
rep_from_s = 0.9

ret_to_s = 0.5
ret_from_s = 1.5

qut_to_s = 0.6
qut_from_s = 1.5


### Define functions for primary and secondary ratings

In [11]:
def to_user_tid_score(tid, uid, type, origin_tid, origin_uid):
    ''' This function used for calculate primary rating matrix.
    
    This function get some information of a tweet and Returns
    the score that two users (the user who posted this tweet
    and the user who posted the original tweet and has now
    been replied to, retweeted, or quoted by this tweet)
    give to these two tweets FOR EACH USER.

    The output is a list of tuples, where each tuple contains
    a user ID and a list of tweets that have been rated (along
    with the value of the rating).
    Output format: [((u_i, ((t_j, s_ij),)) ...]
    '''
    
    origin_tid = [i for i in origin_tid if i is not None]
    origin_uid = [i for i in origin_uid if i is not None]

    if not origin_tid or not origin_uid:
        return [(uid, [(tid, owner_s)])]

    to_s = rep_to_s if type == "replied" else\
           ret_to_s if type == "retweeted" else\
           qut_to_s if type == "quoted" else\
           0
    from_s = rep_from_s if type == "replied" else\
             ret_from_s if type == "retweeted" else\
             qut_from_s if type == "quoted" else\
             0

    return [(uid, [(tid, owner_s), (origin_tid[0], from_s)]),
            (origin_uid[0], [(tid, to_s)]),
           ]


def to_tid_user_score(tid, uid, type, origin_tid, origin_uid):
    ''' This function used for secondary rating.

    This function get some information of a tweet and Returns
    the score that two users (the user who posted this tweet
    and the user who posted the original tweet and has now
    been replied to, retweeted, or quoted by this tweet)
    give to these two tweets FOR EACH TWEET.

    The output is a list of tuples, where each tuple contains
    a tweet ID and a tuple list of users rate to it (along with
    the value of the rating).
    Output format: [(tid_i, ((u_j, s_ij), ...)), ...]
    '''
    if uid != q_uid and origin_uid != q_uid:
        return []
    
    origin_tid = [i for i in origin_tid if i is not None]
    origin_uid = [i for i in origin_uid if i is not None]

    if not origin_tid or not origin_uid:
        return [(tid, ((uid, owner_s),))]

    to_s = rep_to_s if type == "replied" else\
           ret_to_s if type == "retweeted" else\
           qut_to_s if type == "quoted" else\
           0
    from_s = rep_from_s if type == "replied" else\
             ret_from_s if type == "retweeted" else\
             qut_from_s if type == "quoted" else\
             0

    return [(tid, ((uid, owner_s), (origin_uid[0], to_s),)),
            (origin_tid[0], ((uid, from_s),)),
           ]


def extract_tuples(tweet_info, func):
    '''
    This function extract some information of tweet and send it
    to one of the following funcions and return their results:
    - to_user_tid_score
    - to_tid_user_score
    '''
    return func(
        tweet_info.get('id'),
        tweet_info["user"].get('id'),
        tweet_info.get('tweet_type'),
        [
            tweet_info.get('in_reply_to_status_id_str', None),
            tweet_info.get('quoted_status', {}).get('id'),
            tweet_info.get('retweeted_status', {}).get('id'),
        ],
        [
            tweet_info.get('in_reply_to_user_id_str', None),
            tweet_info.get('quoted_status', {}).get('user', {}).get('id'),
            tweet_info.get('retweeted_status', {}).get('user', {}).get('id'),
        ],
    )


def extract_relations(x):
    '''
    This function extracts relationships between users who interacted
    with this tweet.
    
    x contains the tweet_id (tid) and a list of tuples. Each tuple
    contains a user_id (u) and its interaction with the tweet (score
    given to the tweet).
    x: (tid, [(u1, s1), ...])

    The output is a list that the single element of it, contains the user_id
    (q_uid) and a list of tuples. Each tuple contains a tweet_id (tid), 
    second user_id that has relation to q_uid (called u2), and the score
    given by each of these two users to this tweet (s1 and s2 respectively)
    output: 
    [(q_uid, [(tid, u2, s1, s2),
            (tid, u3, s1, s3),
            ...
           ])
    ]
    
    '''

    tid, user_score = x

    for (u1, s1) in user_score:
        if u1 == extract_relations.q_uid:
            u1_relations = []
            for (u2, s2) in user_score:
                if u1 != u2 and s1 > rep_to_s:
                    u1_relations.append((tid, u2, s1, s2))
            if u1_relations:
                return [(u1, sorted(u1_relations, key=lambda x: -x[2]*x[3])[:min(100, len(u1_relations))])]
        
    return [(None,[])]


def find_user_favorites(x, user_scores):
    ''' 
        user_scores: {ui: [(t_j, s_ij), ...]}
        x: (u1, ((tid, uj, s1, sj), ...))
    '''
    th = 0.05
    u, relations = x
    favorite = {}
    if relations:
        for (tid, uj, s1, s2) in relations:
            favorite[tid] = favorite.get(tid, 0) + s1
            for (t, s) in user_scores.get(uj, []):
                favorite[t] = favorite.get(t, 0) + s1*s2*s

    if favorite:
        max_favorite = max(favorite.values())
        th = 0.05 * max_favorite
        while len(favorite) > 100:
            favorite = {t:i for t,i in favorite.items() if i > th}
            th *= 1.1
        return (u, favorite)
    return (u, {})


### Calculating Primary rating Matrix

In [12]:
start_calculating_matrix = datetime.datetime.now()
print(start_calculating_matrix)


2024-02-04 13:55:15.098258


In [13]:
# [((u_i, ((t_j, s_ij),)), ...]
user_tid_score_rdd = tweets_rdd.flatMap(
    lambda x: extract_tuples(json.loads(x), func=to_user_tid_score))

# [(u_i, ((t_j, s_ij), ...)), ...]
user_tids_scores_rdd = user_tid_score_rdd.reduceByKey(
    lambda x, y: x if not x.extend(y) else x)

user_scores_list = user_tids_scores_rdd.collect()

user_scores_dict = dict(user_scores_list)


### Extracting the selected user's favorite tweet IDs using rating matrix


In [14]:
start_extracting_tweets_id_t = datetime.datetime.now()
print(start_extracting_tweets_id_t)

2024-02-04 13:55:49.470873


In [15]:
# [(tid, [(u, s)]), ...]
tid_user_score_rdd = tweets_rdd.flatMap(lambda x: extract_tuples(json.loads(x), func=to_tid_user_score))

# [(tid, [(u, s), ...]), ...]
tid_users_scores_rdd = tid_user_score_rdd.reduceByKey(lambda x, y: x + y)

# [(q_uid, [(tid, u2, s1, s2)])]
extract_relations.q_uid = q_uid
user_relation_rdd = tid_users_scores_rdd.flatMap(extract_relations)\
                                         .filter(lambda x: x[1])

# [(q_uid, [(tid, u2, s1, s2), ...])]
user_relations_rdd = user_relation_rdd.reduceByKey(lambda x, y: x if not x.extend(y) else x)


In [16]:
# Take query user's relations in ram
user_relations = user_relations_rdd.take(1)[0]

# Find the ID of the user's favorite tweets
user_favorites = find_user_favorites(x=user_relations, user_scores=user_scores_dict)



In [17]:
user_favorites

('1365385186364567553',
 {'1736435583671558501': 190.59000000000017,
  '1735599258131144851': 297.6000000000002,
  '1734860866737082788': 469.07999999999817,
  '1735268252509483070': 205.95000000000007,
  '1736040658391924783': 430.7699999999992,
  '1735673840787726439': 198.23000000000013,
  '1735544221094875415': 259.4700000000002,
  '1735000316972572900': 309.5399999999989,
  '1734986413844668664': 412.70999999999793,
  '1736422359727235528': 218.42000000000004,
  '1736764666083205541': 249.98000000000025,
  '1734643914647183759': 289.4599999999997,
  '1735364749833986160': 379.22999999999956,
  '1736107127339462907': 277.7099999999997,
  '1736097735814598935': 478.2299999999995,
  '1735790675310891266': 262.3099999999995,
  '1736175221697106332': 219.33000000000018,
  '1734610051967725921': 199.14000000000024,
  '1735706263315431557': 331.6699999999982,
  '1734065865878843514': 226.2400000000001,
  '1734069352645746810': 339.03999999999985,
  '1735638863580696835': 227.290000000000

In [18]:
if not user_favorites:
    print('Please choose another User ID, this user has no favorite tweet in this database')

### Extract and Show selected user's tweets and the his/her favorite tweets information

In [19]:
start_extract_and_show_tweets_t = datetime.datetime.now()
print(start_extract_and_show_tweets_t)


2024-02-04 13:56:19.007119


In [20]:
necessary_keys = ['tweet_type', 'user', 'id','text', 'name', 'screen_name', 
                  'in_reply_to_status_id_str', 'in_reply_to_user_id_str',
                  'quoted_status', 'retweeted_status','profile_image_url',
                 ]


In [21]:
favorites_tweets = tweets_rdd.filter(lambda x: json.loads(x)['id'] in user_favorites[1].keys() or
                                               json.loads(x)['user']['id'] == q_uid)\
                             .map(lambda x: dict(filter(lambda y: y[0] in necessary_keys, json.loads(x).items())))\
                             .collect()
favorites_tweets2 = favorites_tweets.copy()


### Define functions needed to separate tweets based on tweet_type and display tweets appropriately

In [22]:
def extract_user_origin_tweets(tweets, uid, rem=True):
    origin_tweets = []
    for t in tweets:
        if t['tweet_type'] == 'generated':
            if t.get('user',{}).get('id','0') == uid:
                origin_tweets.append(t)
    if rem:
        for t in origin_tweets:
            tweets.remove(t)
    return origin_tweets


def extract_user_replied_tweets(tweets, uid, rem=True):
    replied_tweets = []
    for t in tweets:
        if t['tweet_type'] == 'replied':
            if t.get('user',{}).get('id','0') == uid:
                replied_tweets.append(t)
    if rem:
        for t in replied_tweets:
            tweets.remove(t)
    return replied_tweets


def extract_user_quoted_tweets(tweets, uid, rem=True):
    quoted_tweets = []
    for t in tweets:
        if t['tweet_type'] == 'quoted':
            if t.get('user',{}).get('id','0') == uid:
                quoted_tweets.append(t)
    if rem:
        for t in quoted_tweets:
            tweets.remove(t)
    return quoted_tweets


def extract_user_retweeted_tweets(tweets, uid, rem=True):
    retweeted_tweets = []
    for t in tweets:
        if t['tweet_type'] == 'retweeted':
            if t.get('user',{}).get('id','0') == uid:
                retweeted_tweets.append(t)
    if rem:
        for t in retweeted_tweets:
            tweets.remove(t)
    return retweeted_tweets


def extract_replied_to_user_tweets(tweets, uid, rem=True):
    replied_tweets = []
    for t in tweets:
        if t['tweet_type'] == 'replied':
            if t.get('in_reply_to_user_id_str', '0') == uid:
                replied_tweets.append(t)
    if rem:
        for t in replied_tweets:
            tweets.remove(t)
    return replied_tweets


def extract_quoted_user_tweets(tweets, uid, rem=True):
    quoted_tweets = []
    for t in tweets:
        if t['tweet_type'] == 'quoted':
            if t.get('quoted_status', {}).get('user', {}).get('id', '0') == uid:
                quoted_tweets.append(t)
    if rem:
        for t in quoted_tweets:
            tweets.remove(t)
    return quoted_tweets


def extract_retweeted_user_tweets(tweets, uid, rem=True):
    retweeted_tweets = []
    for t in tweets:
        if t['tweet_type'] == 'retweeted':
            if t.get('retweeted_status', {}).get('user', {}).get('id', '0') == uid:
                retweeted_tweets.append(t)
    if rem:
        for t in retweeted_tweets:
            tweets.remove(t)
    return retweeted_tweets


def extract_explore_tweets(tweets):
    return tweets


def show_tweets(tweets, tweets_type):
    print('-'*100)
    print(f'Number of {tweets_type}:', len(tweets), '\n')
    ts = [t['text'].replace('\u200c', '').split('\n') for t in tweets]
    for t in ts:
        print('-'*100)
        for line in t:
            print(line)
    print('-'*100)


### Separate tweets based on tweet_type and display them

In [23]:
uid = q_uid
favorites_tweets = favorites_tweets2.copy()
user_origin_tweets = extract_user_origin_tweets(favorites_tweets, uid)
user_quoted_tweets  = extract_user_quoted_tweets(favorites_tweets, uid)
user_retweeted_tweets  = extract_user_retweeted_tweets(favorites_tweets, uid)
user_replied_tweets  = extract_user_replied_tweets(favorites_tweets, uid)
replied_to_user_tweets  = extract_replied_to_user_tweets(favorites_tweets, uid)
quoted_user_tweets  = extract_quoted_user_tweets(favorites_tweets, uid)
retweeted_user_tweets  = extract_retweeted_user_tweets(favorites_tweets, uid)
explore_tweets = extract_explore_tweets(favorites_tweets)


In [24]:
show_tweets(user_origin_tweets, 'user_origin_tweets')

----------------------------------------------------------------------------------------------------
Number of user_origin_tweets: 57 

----------------------------------------------------------------------------------------------------
دوستان برام بسیارغم انگیزتر و ناراحت کننده تر اینه که رهبر معظم و افرادهم فکر ایشان  که برای سیرتاپیاز مردم نظریه پردازی می کنند حتی اشاره وانتقادکوچکی درقبال هحمه ی خودخواسته ی 15 میلیون قاتل ومتجاوزبعنف ودزد #افغانستانی به مردم خودشان وکشته شدن روزانه مردم بدست اینها نکرده اند!
----------------------------------------------------------------------------------------------------
نه کوچکترین قرابت نژادی داریم!،نه کوچکترین قرابت فرهنگی!،نه کوچکترین قرابت مذهبی!،فقط هردوی مابه فارسی صحبت می کنیم همین!بنابراین رویای ترمیم بافت جمعیتی #ایران باواردات گله ای این #وحوش آدمکش ولواط کار رویایی  آشفته وبی تعبیر است که فقط میتواندازمغزهای زنگ زده ساطع شده باشد! https://t.co/3tnVdVr3IG
--------------------------------------------------------------------------------

In [25]:
show_tweets(user_quoted_tweets, 'user_quoted_tweets')


----------------------------------------------------------------------------------------------------
Number of user_quoted_tweets: 636 

----------------------------------------------------------------------------------------------------
#اخراج_افغانی_مطالبه_ملی 
#سیستم_اعتبار_سنجی 
#رمز_ریال
 #فایو_جی 

در صورت شروع حمله طالبان در عمق خاک ما و هر دشمنی ۶۰میلیون ایران واکسن زده و۸۰درصد جمعیت کشورتوان دفاعی ندارن چون با ارسال فرکانس بالای سلاح امواج فایوجی (اینترنت نسل پنجم )درجا کشته میشن!

قبلا توی عراق تست شده https://t.co/Jqklu8t3G2
----------------------------------------------------------------------------------------------------
اگر بر مدار عقل هم نباشیم و حساب سود و زیان هم نکنیم حضور این حجم از #افغانستانی دزد و قاتل و بدفرهنگ در میان مردم ایران یعنی مرگ تدریجی #ایران و #ایرانی!!
#اخراج_بیقید_شرط_تمام_افاغنه 
#اخراج_افغانی_مطالبه_ملی
----------------------------------------------------------------------------------------------------
اگر بر مدار عقل هم نباشیم و حساب سود و زیان ه

In [26]:
show_tweets(user_retweeted_tweets, 'user_retweeted_tweets')


----------------------------------------------------------------------------------------------------
Number of user_retweeted_tweets: 1864 

----------------------------------------------------------------------------------------------------
دوستان برام بسیارغم انگیزتر و ناراحت کننده تر اینه که رهبر معظم و افرادهم فکر ایشان  که برای سیرتاپیاز مردم نظریه پردازی می کنند حتی اشاره وانتقادکوچکی درقبال هحمه ی خودخواسته ی 15 میلیون قاتل ومتجاوزبعنف ودزد #افغانستانی به مردم خودشان وکشته شدن روزانه مردم بدست اینها نکرده اند!
----------------------------------------------------------------------------------------------------
به نظرتون افغانی ها   میتونن غیر قانونی از مرز رد بشن و تو قلب تهران با لباس سنتی تردد کنن بدون ترس از این که ممکنه رد مرز بشن ؟؟!!!!علتش چیه ؟!!
#اخراج_افغانی_مطالبه_ملی https://t.co/LXQumona42
----------------------------------------------------------------------------------------------------
این فرد یعنی #محسن_پهلوان مدیرعامل #پدیده_شاندیز بعنوان یکی از مفسدان بزرگ ایران

In [27]:
show_tweets(user_replied_tweets, 'user_replied_tweets')


----------------------------------------------------------------------------------------------------
Number of user_replied_tweets: 292 

----------------------------------------------------------------------------------------------------
@SaeedKoushafar این پارادوکس زمانی ممکن و قابل تفسیر هست که آن دزدی ها مستقیما به جیب نظام جمهوری اسلامی واریز شده و یا شتیل بسیار درشت نظام جمهوری اسلامی هم پرداخت شده باشد!! در این نظام سبیل نظام را همیشه چرب نگه دار و به دزدی هایت ادامه بده نظام هیچ مشکلی با تو نخواهد داشت! 😂😂😂
----------------------------------------------------------------------------------------------------
@ahmadjafari100 اگر فرض کنیم دولتمردان دولت #حسن_روحانی به عصر انسانهای نئاندرتال تعلق داشتند دولتمردان دولت #ابراهیم_رئیسی از موجودات بازمانده از عصر ژوراسیک محسوب خواهند شد!! 😂😂😂
----------------------------------------------------------------------------------------------------
@AliReza9119 اتفاقا من مسئله ام اینست که چرابجای #افغانستانی سلفی آن هم 15 میلیون نفرکه نه درکشو

In [28]:
show_tweets(explore_tweets, 'explore_tweets')


----------------------------------------------------------------------------------------------------
Number of explore_tweets: 88 

----------------------------------------------------------------------------------------------------
هر دم ازاین باغ بری میرسد
تازه تر از تازه تری میرسد
کودکان #افغانستانی دستگاه پوز بانکی گرفته و در خیابانهای #مشهد دست فروشی میکنند.
تنها شغل باقیمانده زنان سرپرست و مردان ازکار افتاده ایرانی هم به دست کودکان #مهاجر_افغانی افتاد. https://t.co/pini1CH7VW
----------------------------------------------------------------------------------------------------
♦️بازداشت ۲ سارق افغان تجهیزات ایستگاه متروی صادقیه

فرمانده یگان انتظامی متروی تهران:
🔹در تاریخ ۱۹ آذر ماموران پلیس مترو مطلع شدند افرادی به قصد سرقت کابل و تجهیزات مترو وارد ایستگاه صادقیه شده و مقدار زیادی تجهیرات را سرقت کرده و از مترو متواری شدند.
#اخراج_افغانی_مطالبه_ملی
----------------------------------------------------------------------------------------------------
درود بر هموطنان عزیز و با غیرت اس

In [29]:
end_tweet_recommending_t = datetime.datetime.now()
print(end_tweet_recommending_t)
print("The total time spent finding and displaying the user's favorite tweets:",
      end_tweet_recommending_t-start_calculating_matrix)


2024-02-04 13:56:49.310181
The total time spent finding and displaying the user's favorite tweets: 0:01:34.211923


## User Recommender 

### Extract Tweets of recommended Users

In [30]:
start_user_recommending_t = datetime.datetime.now()
print(start_user_recommending_t)


2024-02-04 13:56:49.314999


In [31]:
def extract_users(x):
    tweet_info = json.loads(x)

    uids = [tweet_info["user"].get('id')]

    origin_uid = [tweet_info.get('in_reply_to_user_id_str', None),
                  tweet_info.get('quoted_status', {}).get('user', {}).get('id'),
                  tweet_info.get('retweeted_status', {}).get('user', {}).get('id'),
                 ]

    origin_uid = [i for i in origin_uid if i is not None]

    if origin_uid:
        uids.append(origin_uid[0])
    
    return uids

In [32]:
recommended_users = tweets_rdd.filter(lambda x: json.loads(x)['id'] in user_favorites[1].keys() or
                                               json.loads(x)['user']['id'] == q_uid)\
                              .flatMap(extract_users).collect()

In [33]:
counts = Counter(recommended_users)
mcru = counts.most_common(20)  # most_common_recommended_users
mcru_id, repeats = zip(*mcru[1:])
mcru[1:]

[('995619189485391873', 139),
 ('1684786665024282624', 91),
 ('1331878979964334080', 70),
 ('1721287461140099072', 52),
 ('1682143930119323650', 47),
 ('1718268858056736768', 47),
 ('1638175211366543365', 42),
 ('1722750067453366272', 40),
 ('1042184336018161664', 35),
 ('1088222529041416193', 35),
 ('1624707516327141378', 31),
 ('1067468128806989824', 30),
 ('1597569274448695304', 30),
 ('1716147579954634752', 30),
 ('1016273630572007424', 29),
 ('1638038934356729856', 28),
 ('1408332971262693377', 27),
 ('1613244744292786184', 26),
 ('993203075686043656', 23)]

### Show Tweets of recommended Users

In [34]:
start_extract_recommended_users_tweets_t = datetime.datetime.now()
print(start_extract_recommended_users_tweets_t)


2024-02-04 13:57:20.116678


In [35]:
rec_users_tweets = tweets_rdd.filter(lambda x: json.loads(x)['user']['id'] in mcru_id)\
                            .map(lambda x: dict(filter(lambda y: y[0] in necessary_keys, json.loads(x).items())))\
                            .collect()



In [36]:
end_extract_recommended_users_tweets_t = datetime.datetime.now()
print(end_extract_recommended_users_tweets_t)



2024-02-04 13:57:41.581477


#### Tweets of Query User

In [37]:
favorites_tweets = favorites_tweets2.copy()
print('','#'*100,'\n', 'Tweets of Query User\n', '#'*100,'\n')
show_tweets(extract_user_origin_tweets(favorites_tweets, q_uid, rem=False), 'user_origin_tweets')
show_tweets(extract_user_quoted_tweets(favorites_tweets, q_uid, rem=False), 'user_quoted_tweets')
show_tweets(extract_user_retweeted_tweets(favorites_tweets, q_uid, rem=False), 'user_retweeted_tweets')
show_tweets(extract_user_replied_tweets(favorites_tweets, q_uid, rem=False), 'user_replied_tweets')

 #################################################################################################### 
 Tweets of Query User
 #################################################################################################### 

----------------------------------------------------------------------------------------------------
Number of user_origin_tweets: 57 

----------------------------------------------------------------------------------------------------
دوستان برام بسیارغم انگیزتر و ناراحت کننده تر اینه که رهبر معظم و افرادهم فکر ایشان  که برای سیرتاپیاز مردم نظریه پردازی می کنند حتی اشاره وانتقادکوچکی درقبال هحمه ی خودخواسته ی 15 میلیون قاتل ومتجاوزبعنف ودزد #افغانستانی به مردم خودشان وکشته شدن روزانه مردم بدست اینها نکرده اند!
----------------------------------------------------------------------------------------------------
نه کوچکترین قرابت نژادی داریم!،نه کوچکترین قرابت فرهنگی!،نه کوچکترین قرابت مذهبی!،فقط هردوی مابه فارسی صحبت می کنیم همین!بنابراین رویای ترمیم بافت جمعیت

#### Tweets of Recommended User

In [38]:
for (recommended_uid, rep) in mcru[1:]:
    print('','#'*100,'\n', f'User ID: {recommended_uid}, repetitions: {rep}\n', '#'*100,'\n')
    show_tweets(extract_user_origin_tweets(rec_users_tweets, recommended_uid, rem=False), 'user_origin_tweets')
    show_tweets(extract_user_quoted_tweets(rec_users_tweets, recommended_uid, rem=False), 'user_quoted_tweets')
    show_tweets(extract_user_retweeted_tweets(rec_users_tweets, recommended_uid, rem=False), 'user_retweeted_tweets')
    show_tweets(extract_user_replied_tweets(rec_users_tweets, recommended_uid, rem=False), 'user_replied_tweets')



 #################################################################################################### 
 User ID: 995619189485391873, repetitions: 139
 #################################################################################################### 

----------------------------------------------------------------------------------------------------
Number of user_origin_tweets: 62 

----------------------------------------------------------------------------------------------------
به قول پاکستانی های #نمک_حرام_افغانی 

چرا تعداد بی صفت ها در میان اینها زیاد هست؟
امروز بسیاری از آنها حاضر هستند اجر جهاد خودشان را به یک ادعا در مورد کشور ما به باد دهند و در نهایت با پر رویی به ما که به آنها صدقه دادیم فحاشی می کنند  #اخراج_افغانی_مطالبه_ملی https://t.co/kal2fUruol
----------------------------------------------------------------------------------------------------
وضعیت نیروی مرزبانی کشور بدون جاده و خودرو زره پوش که باید در کوهستان های بلوچستان گشت بزند و اینچنین در کمین بیافتد

فیل

In [39]:
end_notebook_t = datetime.datetime.now()
print(end_notebook_t,'\n')

2024-02-04 13:57:41.775207 



In [40]:
print("The total time spent for showing a sample of tweets, count tweets and get users:", str(start_calculating_matrix - start_notebook_t).split('.')[0])
print("The total time spent for calculating Primary Rating Matrix:                     ", str(start_extracting_tweets_id_t - start_calculating_matrix).split('.')[0])
print("The total time spent for extracting Recommended Tweets' ID:                     ", str(start_extract_and_show_tweets_t - start_extracting_tweets_id_t).split('.')[0])
print("The total time spent for extract and show Tweets:                               ", str(start_user_recommending_t - start_extract_and_show_tweets_t).split('.')[0])
print("The total time spent for extracting Recommended Ussers:                         ", str(start_extract_recommended_users_tweets_t - start_user_recommending_t).split('.')[0])
print("The total time spent for extract and show Tweets' of Recommended Users:         ", str(end_extract_recommended_users_tweets_t - start_extract_recommended_users_tweets_t).split('.')[0])
print('_'*90)
print("The total time spent for this script:                                           ", str(end_notebook_t-start_notebook_t).split('.')[0])


The total time spent for showing a sample of tweets, count tweets and get users: 0:01:08
The total time spent for calculating Primary Rating Matrix:                      0:00:34
The total time spent for extracting Recommended Tweets' ID:                      0:00:29
The total time spent for extract and show Tweets:                                0:00:30
The total time spent for extracting Recommended Ussers:                          0:00:30
The total time spent for extract and show Tweets' of Recommended Users:          0:00:21
__________________________________________________________________________________________
The total time spent for this script:                                            0:03:35
